This notebook attempts to predict the effectiveness of different types of apps for epidemiological contact tracing. Initial (and still very rough) version by Peter Eckersley <peter.eckersley@gmail.com> and Lewis Mitchell <lewis.mitchell@adelaide.edu.au>; feel free to reuse and repurpose, but please indicate that (as of this version) results are not peer reviewed, and do not imply endorsement of any conclusion or policy!


In [0]:
import numpy as np
import numpy.random as npr
import bokeh.plotting as bp
import bokeh.io as bi
import bokeh.util.hex as bh
import bokeh.transform as bt
import bokeh.models as bm
import bokeh.colors as bc

In [0]:
# we use a Monte Carlo approach to handle uncertainty in parameters; we call down to an SEIRQ 
# differential equation pandemic model to estimate # of lives saved
samples = 30000

# model the United States
N = 327 * 10**6
# start date is beginning of February 2020

# Variables for our model

data_raw = dict(
  # These are for the app
  pop_adoption = npr.uniform(0, 1.0, size=samples),  # independent variable, explore all adoption levels
  #pop = 1 / npr.pareto(1e6, size=samples),  # scale of population, roughly cities to countries
  tester_adoption = npr.uniform(0.3, 1.0, size=samples),  # when a test is positive, does that wind up in the app?
  testing_rate = np.clip(npr.pareto(1, size=samples), 0, 1),  # Fraction of infections that get tested. Typical range from 0.001 (US or Indonesia) to above 0.5 (Singapore)
  catch_rate_bt = npr.uniform(0.4, 0.8, size=samples),  # how often does the software detect the contact between two of its users XXX needs more modelling
  catch_rate_gps = npr.uniform(0.3, 0.8, size=samples),  # assume GPS is less precise and might fail worse, though best case is as good because of intertemporal fomite risk detection
)

pandemic_params = dict(
  # these are for the pandemic
  #r0 = (1.5 + npr.beta(2, 5, size=samples) * 3),  # TODO: ground better in https://github.com/midas-network/COVID-19/tree/master/parameter_estimates/2019_novel_coronavirus#basic-reproduction-number
  r0 = npr.uniform(1.5, 3.5, size=samples),
  app_launch_date = npr.uniform(65, 90, size=samples),  # days from 2020-02-01
  #infection_fatality_rate = npr.uniform(0.11, 4.3, size=samples)/100,  # follow https://www.medrxiv.org/content/medrxiv/early/2020/03/09/2020.03.05.20031773.full.pdf
                                                                       # but err a little higher due to subsequent Diamond Princess deaths & ICU overload risks
  infection_fatality_rate = npr.beta(2, 5, size=samples)*4./100,
  # could use npr.lognormal(-0.1, 0.9, size=samples)
  lockdown_threshold = npr.pareto(100, size=samples).clip(1e-5, 0.02),
  lockdown_effect = npr.uniform(0.3, 0.9, size=samples)
  #lockdown_effect = np.ones(samples),
  #lockdown_date = npr.uniform(55, 75, size=samples),
  #lockdown_r0 = npr.uniform(1.3 / 2.4, 0.8 / 34, size=samples),
  #relaxation_date = npr.uniform(14, 60, size=samples),
  #relaxation_r0 = np.sqrt(r0 * lockdown_r0)  # after economy resumes, r0 goes to geometric mean
)
data_raw.update(pandemic_params)
data_raw["tester_adoption"] = np.minimum(data_raw["tester_adoption"], data_raw["pop_adoption"])  # assume that if you have very high population adoption, testers probably use this too
globals().update(data_raw)  # refactorme out
data = bm.ColumnDataSource(data_raw)

In [0]:
def display(plot):
  bi.curdoc().add_root(plot)
  bp.output_notebook()
  bi.show(plot)

In [0]:
# summary of each simulation for the tooltip
tooltips_bt = [
    ("societal adoption", "@pop_adoption"),
    ("tester adoption", "@tester_adoption"),
    ("testing rate", "@testing_rate"),
    ("app contact detection rate", "@catch_rate_bt"),  # needs to change
    ("trace success rate", "$y")
]

tooltips_gps = tooltips_bt[:]
tooltips_gps[-2] = ("app contact detection rate", "@catch_rate_gps")

In [0]:
def coverage1(adoption, testing_rate, tester_adoption, catch_rate):
  """
  Tramsmission event coverage for an app that needs to be on both users' phones, at the time of
  exposure, eg by bluetooth matching. *NOTE* this assumes iOS and Android can see each other.
  If not, coverage is roughly halved :(
  """
  intersection = adoption * adoption
  return intersection * testing_rate * tester_adoption * catch_rate

cov_bt = coverage1(pop_adoption, testing_rate, tester_adoption, catch_rate_bt)
data.add(cov_bt, "cov_bt")

'cov_bt'

In [0]:
step = 0.03
incs = np.arange(0, 1, step)

def bin_stats(variable, statistic, group_by=pop_adoption):
  bins = [[] for n in incs]

  for adoption, v in zip(group_by, variable):
    i = int(adoption // step)
    bins[i].append(v)

  binned = np.array([statistic(b) for b in bins])
  return binned

bin_averages = lambda data: bin_stats(data, np.average)
bin_25 = lambda data: bin_stats(data, lambda x: np.quantile(x, 0.25))
bin_75 = lambda data: bin_stats(data, lambda x: np.quantile(x, 0.75))

avgs = bin_averages(cov_bt)

Now compare to an app where the assumption is that diagnosed patients contribute to an anonymous redzone map based on retrospective location history

In [0]:

onboarding_loss = npr.uniform(0.1, 0.6, size=samples)  # patients who refuse or fail to install the app at diagnosis time
onboarding_loss = np.minimum(onboarding_loss, 1 - pop_adoption)  # but if 100% of users have the app, diagnosed patients do too

def coverage2(adoption, testing_rate, tester_adoption, catch_rate2):
  return adoption * testing_rate * tester_adoption * catch_rate2 * (1 - onboarding_loss)

cov2 = coverage2(pop_adoption, testing_rate, tester_adoption, catch_rate_gps)
data.add(cov2, "cov_gps")
avgs2 = bin_averages(cov2)

In [0]:
plot = bp.figure(x_range=[0,1], y_range=[0, 1], plot_width=768, plot_height=768,
                 x_axis_label="Proportion of population using app",
                 y_axis_label="Proportion of infections traced",
                 #,tooltips=tooltips_bt
                 )
plot.xaxis.axis_label_text_font_size = plot.yaxis.axis_label_text_font_size="16pt"
plot.xaxis.major_label_text_font_size = plot.yaxis.major_label_text_font_size ="11pt"

plot.scatter(x="pop_adoption", y="cov_bt", radius=0.005, fill_alpha=0.2, line_color=None, source=data)
plot.scatter(pop_adoption, cov2, radius=0.005, fill_alpha=0.1, line_color=None, fill_color="#10a080")
plot.line(incs, bin_25(cov_bt), line_color="#0000a0", legend_label="bluetooth +/- 25%", line_width=2.0)
plot.line(incs, bin_75(cov_bt), line_color="#0000a0", line_width=2.0)

plot.line(incs, avgs2, line_color="#005000", legend_label="retrospective gps matching")
plot.line(incs, bin_25(cov2), line_color="#80f080", legend_label="gps +/- 25%")
plot.line(incs, bin_75(cov2), line_color="#80f080")

plot.line(incs, avgs, line_color="#a000f0", legend_label="prospective bluetooth matching", line_width=2.0)  
plot.legend.label_text_font_size = '11pt'

bi.curdoc().add_root(plot)
bp.output_notebook()
bi.show(plot)
print("Monte Carlo simulation of "
      "effectiveness as a function of adoption for bluetooth matching apps (blue) and apps that\n"
      "use retrospective location records such as Google Maps Timeline or iOS's on-device encrypted\n"
      "location records (green).")

Monte Carlo simulation of effectiveness as a function of adoption for bluetooth matching apps (blue) and apps that
use retrospective location records such as Google Maps Timeline or iOS's on-device encrypted
location records (green).


# ---------------------------------------------------------------------------------------------------
# -------- WARNING: (Code below this point is experimental) --------
# ---------------------------------------------------------------------------------------------------

In [0]:
import numpy as np
import numpy.random as npr
import matplotlib.pyplot as plt
# import EoN
from scipy.integrate import odeint

In [0]:
def human_format(num):
    num = float('{:.3g}'.format(num))
    magnitude = 0
    while abs(num) >= 1000:
        magnitude += 1
        num /= 1000.0
    return '{}{}'.format('{:f}'.format(num).rstrip('0').rstrip('.'), ['', 'K', 'M', 'B', 'T'][magnitude])

In [0]:
# adapted from https://scipython.com/book/chapter-8-scipy/additional-examples/the-sir-epidemic-model/
t = np.linspace(0, 364, 365)
def simulate_quarantined_epidemic(r0, contact_tracing_rate, app_launch_date, lockdown_threshold, lockdown_effect):
  "Run a simple SEIQR model of an epidemic"
  # solved for infection_rate using https://science.sciencemag.org/content/early/2020/03/24/science.abb3221.full
  infect_rate, recovery_rate = 1./3, 1./2.5
  # Total population, N.
  #N = 25*10**6
  # Initial number of infected and recovered individuals, I0 and R0.
  E0, I0, R_init, Q0 = 100, 0, 0, 0
  L0 = 0.  # days of lockdown
  # Everyone else, S0, is susceptible to infection initially.
  S0 = N - I0 - R_init - E0 - Q0
  # Contact rate, beta, and mean recovery rate, gamma, (in 1/days).
  # A grid of time points (in days)

  # The SEEIIR model differential equations.
  def deriv(y, t, N, base_r0, infect_rate, recovery_rate, contact_tracing_rate,
            lockdown_threshold, lockdown_effect):
      S, E, I, R, Q, L = y

      #if (S < 0) or (E < 0) or (I < 0) or (R < 0) or (Q < 0):
      #    import pdb
      #    pdb.set_trace()

      if I / N > lockdown_threshold:
          r0 = base_r0 * lockdown_effect
          dLdt = 1.
      else:
          r0 = base_r0
          dLdt = 0.

      contact_rate = recovery_rate * r0

      contact_tracing_rate = contact_tracing_rate*np.heaviside(t-app_launch_date,1)
      dSdt = -contact_rate * S * I / N
      dEdt = (1-contact_tracing_rate) * contact_rate * S * I / N - infect_rate * E
      dIdt = infect_rate*E - recovery_rate*I
      dRdt = recovery_rate * I
      # Q represents people who are quarantined *due to the app intervention* ; other
      # types of qurantine should be reflected in the value of R0
      dQdt = contact_tracing_rate*contact_rate * S * I / N
      return dSdt, dEdt, dIdt, dRdt, dQdt, dLdt

  # Initial conditions vector
  y0 = S0, I0, E0, R_init, Q0, L0
  # Integrate the SIR equations over the time grid, t.
  ret = odeint(deriv, y0, t, args=(N, r0, infect_rate, recovery_rate, contact_tracing_rate,
                                   lockdown_threshold, lockdown_effect))
  S, E, I, R, Q, L = ret.T
  return t, I, R, L

In [0]:
# Explore how the app launch day affects dynamics

def display(plot):
  bi.curdoc().add_root(plot)
  bp.output_notebook()
  bi.show(plot)

plot = bp.figure(plot_width=768, plot_height=400, y_axis_type="linear", y_range=[0, 0.1],
                 x_axis_label="Day", y_axis_label="Infected",
                 title="Illustrate the basic dynamics of the epidemic model for different app "
                       "launch dates (c")
base_r0 = 2.4

color_mapper = bm.LinearColorMapper(palette="Viridis256", low=20, high=150)

for launch_date in range(20, 150, 3):
  t, I, R, L = simulate_quarantined_epidemic(2.4, 0.2, launch_date, 0.001, 0.8)
  #plot.line(t, I/N, line_color=bc.RGB(0, launch_date * 2, 200))
  kwargs = {"legend_label" : "days of quarantine"} if launch_date == 20 else {}
  plot.line(t, I/N, line_color=color_mapper.palette[int((launch_date-20)*255/130.)], alpha=0.6)
  plot.line(t, 0.1 * L/365., line_color = "red", alpha=0.2, **kwargs)

#eg = np.piecewise(t, [t < 53, t > 105], [base_r0, base_r0, base_r0 * 0.9 / 2.4])
#plot.extra_y_ranges = {"r0": bm.Range1d(start=0, end=3)}
#plot.add_layout(bm.LinearAxis(y_range_name="r0"), 'right')
#plot.line(t, eg, line_color="green", y_range_name="r0", legend_label="r0")

color_bar = bm.ColorBar(color_mapper=color_mapper, label_standoff=12, border_line_color=None, location=(0,0))
plot.add_layout(color_bar, 'right')

display(plot)

In [0]:
print(dir(color_mapper))
color_mapper.palette[101]

['__cached_all__overridden_defaults__', '__cached_all__properties__', '__cached_all__properties_with_refs__', '__class__', '__container_props__', '__delattr__', '__dict__', '__dir__', '__doc__', '__eq__', '__format__', '__ge__', '__getattribute__', '__gt__', '__hash__', '__init__', '__init_subclass__', '__le__', '__lt__', '__module__', '__ne__', '__new__', '__properties__', '__properties_with_refs__', '__qualified_model__', '__reduce__', '__reduce_ex__', '__repr__', '__setattr__', '__sizeof__', '__str__', '__subclasshook__', '__view_model__', '__view_module__', '__weakref__', '_attach_document', '_callbacks', '_clear_extensions', '_clone', '_detach_document', '_document', '_event_callbacks', '_id', '_overridden_defaults', '_property_values', '_repr_html_', '_temp_document', '_to_json_like', '_trigger_event', '_unstable_default_values', '_unstable_themed_values', '_update_event_callbacks', 'apply_theme', 'dataspecs', 'dataspecs_with_props', 'document', 'equals', 'high', 'high_color', 'i

'#2A778E'

In [0]:
def assess_intervention(r0, contact_tracing_rate, app_launch_date, IFR, lockdown_threshold, lockdown_effect):
    _t1, _I1, R1, L1 = simulate_quarantined_epidemic(r0, 0, 0, lockdown_threshold, lockdown_effect)
    _t2, _I2, R2, L2 = simulate_quarantined_epidemic(r0, contact_tracing_rate, app_launch_date, lockdown_threshold, lockdown_effect)
    base_fatality = np.round(IFR * R1[-1])
    intervention_fatality = np.round(IFR * R2[-1])
    return base_fatality, intervention_fatality

def run_simulations():
    results, details = [], []
    for n in range(samples):
        _t1, _I1, R1, L1 = simulate_quarantined_epidemic(
            r0, 0, 0, lockdown_threshold[n], lockdown_effect[n])
        _t2, _I2, R2, L2 = simulate_quarantined_epidemic(
            r0, contact_tracing_rate[n], app_launch_date[n], lockdown_threshold[n], lockdown_effect[n])
    base_fatality = np.round(infection_fatality_rate[n] * (R1[-1] + Q1[-1]))
    intervention_fatality = np.round(infection_fatality_rate * (R2[-1] + Q2[-1]))
    results.append([base_fatality, intervention_fatality, base_fatality - intervention_fatality])
    details.append(sim)

In [0]:
simulations = []
# XXX refactor this loop into assess_interventions
for n in range(samples):
  base, intervention = assess_intervention(r0[n], cov_bt[n], app_launch_date[n], infection_fatality_rate[n], lockdown_threshold[n], lockdown_effect[n])
  simulations.append([base, intervention, base - intervention])
  if not((0 <= base <= N) and (0 <= intervention <= N)):
      print("things got weird at", n, "(%s)" % ((base, intervention),))


/usr/local/lib/python3.6/dist-packages/scipy/integrate/odepack.py:248: ODEintWarning: Excess work done on this call (perhaps wrong Dfun type). Run with full_output = 1 to get quantitative information.
  warnings.warn(warning_msg, ODEintWarning)


In [0]:
simulations = np.array(simulations)


In [0]:
base, intervention, diff = np.array(simulations).T


In [0]:
bin_05 = lambda data: bin_stats(data, lambda x: np.quantile(x, 0.05))
bin_95 = lambda data: bin_stats(data, lambda x: np.quantile(x, 0.95))


In [0]:
plot = bp.figure(x_range=[0,1], plot_width=768, plot_height=768,
                 x_axis_label="Proportion of population using app",
                 y_axis_label="Mortality"
                 )
print(type(incs), cov_bt.shape, intervention.shape)

plot.line(incs, bin_averages(intervention), line_color="#0000ff", legend_label="deaths", line_width=2.0)
plot.line(incs, bin_25(intervention), line_color="#0000a0", legend_label="deaths +- 25% quantiles", line_width=1.6)
plot.line(incs, bin_75(intervention), line_color="#0000a0", line_width=1.6)
plot.line(incs, bin_05(intervention), line_color="#101020", legend_label="deaths 5/95% quantiles", line_width=1.2)
plot.line(incs, bin_95(intervention), line_color="#101020", line_width=1.2)


plot.scatter(pop_adoption, diff, radius=0.005, fill_alpha=0.2, fill_color="#50b050", line_color=None)
plot.line(incs, bin_averages(diff), line_color="#008000", legend_label="lives saved", line_width=2.0)
plot.line(incs, bin_25(diff), line_color="#808000", legend_label="lives saved +- 25% quantiles", line_width=1.75)
plot.line(incs, bin_75(diff), line_color="#808000", line_width=1.75)
plot.line(incs, bin_05(diff), line_color="#c0c030", legend_label="lives saved 5/95% quantiles", line_width=1.5)
plot.line(incs, bin_95(diff), line_color="#c0c030", line_width=1.5)

#plot.line(incs, avgs, line_color="#a000f0", legend_label="prospective bluetooth matching",
#          line_width=2.0)  
display(plot)

<class 'numpy.ndarray'> (30000,) (30000,)


In [0]:
# Partial ranked correlation coefficient 

In [0]:
p = bp.figure(tools="", match_aspect=True, background_fill_color='black', y_range=[-1,1])
p.grid.visible = False
hexes=bh.hexbin(pop_adoption, diff/N, 0.005, aspect_scale=1/12.)
print(np.min(pop_adoption), np.max(pop_adoption))
bh.hexbin?
p.hex_tile(q="q", r="r", size=0.1, line_color=None, source=hexes,
           fill_color=bt.linear_cmap('counts', 'Viridis256', 0, max(hexes.counts)))
#bi.show(p)

1.0040719624737626e-05 0.9999341785758974


GlyphRenderer(id='7008', ...)

In [0]:
# try density maps. FIXME: these need to be normalised to not imply that most of the points lie on the
# left...
p = bp.figure(tools="", match_aspect=True, background_fill_color='black')
p.grid.visible = False

hexes=bh.hexbin(pop_adoption, cov_bt, 0.01)
p.hex_tile(q="q", r="r", size=0.1, line_color=None, source=hexes,
           fill_color=bt.linear_cmap('counts', 'Viridis256', 0, max(hexes.counts)/10))
bi.show(p)
p = bp.figure(tools="", match_aspect=True, background_fill_color='#440154')
p.grid.visible = False

hexes=bh.hexbin(pop_adoption, cov2, 0.01)
p.hex_tile(q="q", r="r", size=0.1, line_color=None, source=hexes,
           fill_color=bt.linear_cmap('counts', 'Viridis256', 0, max(hexes.counts)/10))
bi.show(p)

In [0]:
# Neither beta nor lognormal distributions fit Kacharski's
plot = bp.figure(y_axis_label="PDF", y_range=[0,1])
alt_ifr = npr.lognormal(-0.1, 0.9, size=samples).clip(0,8) / 100.

r0_dist = (1.5 + npr.beta(2, 5, size=samples) * 3)/100.

print ("mean", np.mean(r0_dist))


for name, dist, col in [("lognormal IFR", alt_ifr, "red"), ("beta IFR", infection_fatality_rate, "navy"),
                        ("r0", r0/100, "green")]:
    hist, edges = np.histogram(100 * dist, density=True, bins=100)
    plot.quad(top=hist, bottom=0, left=edges[:-1], right=edges[1:],
              fill_color=col, line_color="white", alpha=0.5, legend_label=name)
    
display(plot)

mean 0.02353184858368142


In [0]:
print(np.min(r0), np.max(r0))

1.5000487801856421 3.499902509814342
